# Data Validation

- パッケージインストール後、ランタイムを再起動すること（Colab）

## Setup

### Install the package

In [3]:
!pip install tensorflow-data-validation==0.27.0 requests==2.24.0

  Using cached tensorflow_data_validation-0.27.0-cp37-cp37m-manylinux2010_x86_64.whl (1.3 MB)
     |████████████████████████████████| 61 kB 282 kB/s 
  Using cached tensorflow_metadata-0.27.0-py3-none-any.whl (47 kB)
  Using cached absl_py-0.10.0-py3-none-any.whl (127 kB)
  Using cached joblib-0.14.1-py2.py3-none-any.whl (294 kB)
  Using cached apache_beam-2.31.0-cp37-cp37m-manylinux2010_x86_64.whl (9.7 MB)
  Using cached pyarrow-2.0.0-cp37-cp37m-manylinux2014_x86_64.whl (17.7 MB)
  Using cached tfx_bsl-0.27.1-cp37-cp37m-manylinux2010_x86_64.whl (2.2 MB)
     |████████████████████████████████| 829 kB 8.5 MB/s 
  Using cached avro-python3-1.9.2.1.tar.gz (37 kB)
     |████████████████████████████████| 2.3 MB 25.7 MB/s 
  Using cached dill-0.3.1.1.tar.gz (151 kB)
     |████████████████████████████████| 183 kB 57.0 MB/s 
     |████████████████████████████████| 144 kB 58.7 MB/s 
     |████████████████████████████████| 435 kB 56.4 MB/s 
     |████████████████████████████████| 83 kB 1.7 MB/s 

### Import packages

In [1]:
import logging

import pandas as pd
import tensorflow_data_validation as tfdv
from tensorflow_data_validation.utils import slicing_util
from tensorflow_metadata.proto.v0 import statistics_pb2

## The dataset

### Download the dataset

In [2]:
!mkdir data

In [3]:
# Initial dataset source
DATASET_URL = "http://bit.ly/building-ml-pipelines-dataset"
# Initial local dataset location
LOCAL_FILE_NAME = "data/consumer_complaints_with_narrative.csv"


def download_dataset(url=DATASET_URL):
    """download_dataset downloads the remote dataset to a local path

    Keyword Arguments:
        url {string} --
            complete url path to the csv data source (default: {DATASET_URL})
        local_path {string} --
            initial local file location (default: {LOCAL_FILE_NAME})
    Returns:
        None
    """
    df = pd.read_csv(url, index_col=0)
    df.to_csv(LOCAL_FILE_NAME)
    logging.info("Download completed.")


download_dataset()

### Load the dataset

In [4]:
df = pd.read_csv(LOCAL_FILE_NAME)
df.head()

product  ... consumer_disputed
0   Debt collection  ...                 0
1  Credit reporting  ...                 0
2   Debt collection  ...                 1
3          Mortgage  ...                 0
4      Student loan  ...                 1

[5 rows x 11 columns]

## Experiments

### Generate statistics

In [5]:

stats = tfdv.generate_statistics_from_csv(
    data_location='data/consumer_complaints_with_narrative.csv',
    delimiter=','
)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


In [6]:
stats

datasets {
  num_examples: 66799
  features {
    type: STRING
    string_stats {
      common_stats {
        num_non_missing: 66799
        min_num_values: 1
        max_num_values: 1
        avg_num_values: 1.0
        num_values_histogram {
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 6679.9
          }
          buckets {
            low

In [7]:
tfdv.visualize_statistics(stats)

### Generate schema

In [8]:
schema = tfdv.infer_schema(stats)

In [9]:
schema

feature {
  name: "product"
  type: BYTES
  domain: "product"
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "sub_product"
  value_count {
    min: 1
    max: 1
  }
  type: BYTES
  domain: "sub_product"
  presence {
    min_count: 1
  }
}
feature {
  name: "issue"
  type: BYTES
  domain: "issue"
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "sub_issue"
  value_count {
    min: 1
    max: 1
  }
  type: BYTES
  domain: "sub_issue"
  presence {
    min_count: 1
  }
}
feature {
  name: "consumer_complaint_narrative"
  type: BYTES
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "company"
  type: BYTES
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "state"
  value_count {
    min: 1
    max: 1
  }
  type:

In [10]:
tfdv.display_schema(schema)

Type  Presence Valency              Domain
Feature name                                                                
'product'                       STRING  required                   'product'
'sub_product'                   STRING  optional  single       'sub_product'
'issue'                         STRING  required                     'issue'
'sub_issue'                     STRING  optional  single         'sub_issue'
'consumer_complaint_narrative'   BYTES  required                           -
'company'                        BYTES  required                           -
'state'                         STRING  optional  single             'state'
'zip_code'                       BYTES  optional  single                   -
'company_response'              STRING  required          'company_response'
'timely_response'               STRING  required           'timely_response'
'consumer_disputed'                INT  required                           -

/usr/local/lib/python3.7/dist-packages/tensorflow_data_validation/utils/display_util.py:151: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Values
Domain                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
'product'           'Bank account or service', 'Consumer Loan', 'Credit card', 'Credit reporting', 'Debt collection', 'Money transfers', 'Mortgage', 'Other financial service', 'Payday loan', 'Prepaid card', 'Student loan'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

### Compare datasets

In [11]:
!mkdir -p chapters/data_validation

In [12]:
df.iloc[5000:].to_csv('chapters/data_validation/dataset_1.csv', index=False)
df.iloc[:5000].to_csv('chapters/data_validation/dataset_2.csv', index=False)

In [13]:
!wc -l data/consumer_complaints_with_narrative.csv
!wc -l chapters/data_validation/dataset_1.csv
!wc -l chapters/data_validation/dataset_2.csv

66800 data/consumer_complaints_with_narrative.csv
61800 chapters/data_validation/dataset_1.csv
5001 chapters/data_validation/dataset_2.csv


In [14]:
train_stats = tfdv.generate_statistics_from_csv(
    data_location='chapters/data_validation/dataset_1.csv',
    delimiter=','
)
val_stats = tfdv.generate_statistics_from_csv(
    data_location='chapters/data_validation/dataset_2.csv',
    delimiter=','
)

tfdv.visualize_statistics(
    lhs_statistics=val_stats,
    rhs_statistics=train_stats,
    lhs_name='VAL_DATASET',
    rhs_name='TRAIN_DATASET'
)

In [15]:
anomalies = tfdv.validate_statistics(statistics=val_stats, schema=schema)

In [16]:
tfdv.display_anomalies(anomalies)

In [17]:
anomalies

baseline {
  feature {
    name: "product"
    type: BYTES
    domain: "product"
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "sub_product"
    value_count {
      min: 1
      max: 1
    }
    type: BYTES
    domain: "sub_product"
    presence {
      min_count: 1
    }
  }
  feature {
    name: "issue"
    type: BYTES
    domain: "issue"
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "sub_issue"
    value_count {
      min: 1
      max: 1
    }
    type: BYTES
    domain: "sub_issue"
    presence {
      min_count: 1
    }
  }
  feature {
    name: "consumer_complaint_narrative"
    type: BYTES
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "company"
    type: BYTES
    presence {
      min_fract

### Skew and Drift

In [18]:
tfdv.get_feature(schema, 'company').skew_comparator.infinity_norm.threshold = 0.01
skew_anomalies = tfdv.validate_statistics(
    statistics=train_stats,
    schema=schema,
    serving_statistics=val_stats
)

In [19]:
tfdv.display_anomalies(skew_anomalies)

In [20]:
# Change the threshold to show anomaly
tfdv.get_feature(schema, 'company').skew_comparator.infinity_norm.threshold = 0.005
skew_anomalies = tfdv.validate_statistics(
    statistics=train_stats,
    schema=schema,
    serving_statistics=val_stats
)

In [21]:
tfdv.display_anomalies(skew_anomalies)

/usr/local/lib/python3.7/dist-packages/tensorflow_data_validation/utils/display_util.py:186: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Anomaly short description                                                                                                                                                         Anomaly long description
Feature name                                                                                                                                                                                                                                    
'company'     High Linfty distance between training and serving  The Linfty distance between training and serving is 0.00571643 (up to six significant digits), above the threshold 0.005. The feature value with maximum difference is: Equifax

In [22]:
tfdv.get_feature(schema, 'company').drift_comparator.infinity_norm.threshold = 0.01
drift_anomalies = tfdv.validate_statistics(
    statistics=train_stats,
    schema=schema,
    previous_statistics=val_stats
)

In [23]:
tfdv.display_anomalies(drift_anomalies)

In [24]:
# Change the threshold to show anomaly
tfdv.get_feature(schema, 'company').drift_comparator.infinity_norm.threshold = 0.005
drift_anomalies = tfdv.validate_statistics(
    statistics=train_stats,
    schema=schema,
    previous_statistics=val_stats
)

In [25]:
tfdv.display_anomalies(drift_anomalies)

/usr/local/lib/python3.7/dist-packages/tensorflow_data_validation/utils/display_util.py:186: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Anomaly short description                                                                                                                                                         Anomaly long description
Feature name                                                                                                                                                                                                                                    
'company'     High Linfty distance between current and previous  The Linfty distance between current and previous is 0.00571643 (up to six significant digits), above the threshold 0.005. The feature value with maximum difference is: Equifax

### Slice the dataset

In [26]:
slice_fn1 = slicing_util.get_feature_value_slicer(
    features={'state': [b'CA']}
)
slice_options = tfdv.StatsOptions(slice_functions=[slice_fn1])
slice_stats = tfdv.generate_statistics_from_csv(
    data_location='data/consumer_complaints_with_narrative.csv',
    stats_options=slice_options
)

In [27]:
def display_slice_keys(stats):
    print(list(map(lambda x: x.name, slice_stats.datasets)))


def get_sliced_stats(stats, slice_key):
    for sliced_stats in stats.datasets:
        if sliced_stats.name == slice_key:
            result = statistics_pb2.DatasetFeatureStatisticsList()
            result.datasets.add().CopyFrom(sliced_stats)
            return result
    print('Invalid Slice key')


def compare_slices(stats, slice_key1, slice_key2):
    lhs_stats = get_sliced_stats(stats, slice_key1)
    rhs_stats = get_sliced_stats(stats, slice_key2)
    tfdv.visualize_statistics(lhs_stats, rhs_stats)

In [28]:
tfdv.visualize_statistics(get_sliced_stats(slice_stats, 'state_CA'))

In [29]:
compare_slices(slice_stats, 'state_CA', 'All Examples')